In [1]:
import os
import h2o
import pandas as pd
import numpy as np
from h2o.automl import H2OAutoML
import tools
from sklearn.experimental import enable_iterative_imputer
from sklearn.impute import IterativeImputer
from sklearn.model_selection import StratifiedKFold

In [2]:
h2o.init()

Checking whether there is an H2O instance running at http://localhost:54321 ..... not found.
Attempting to start a local H2O server...
  Java Version: java version "1.8.0_341"; Java(TM) SE Runtime Environment (build 1.8.0_341-b10); Java HotSpot(TM) 64-Bit Server VM (build 25.341-b10, mixed mode)
  Starting server from /Users/aaran/opt/anaconda3/envs/tensorflow/lib/python3.10/site-packages/h2o/backend/bin/h2o.jar
  Ice root: /var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/tmps9w_gvsx
  JVM stdout: /var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/tmps9w_gvsx/h2o_aaran_started_from_python.out
  JVM stderr: /var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/tmps9w_gvsx/h2o_aaran_started_from_python.err
  Server is running at http://127.0.0.1:54321
Connecting to H2O server at http://127.0.0.1:54321 ... successful.


--------------------------  -----------------------------
H2O_cluster_uptime:         03 secs
H2O_cluster_timezone:       America/Toronto
H2O_data_parsing_timezone:  UTC
H2O_cluster_version:        3.38.0.4
H2O_cluster_version_age:    2 months and 16 days
H2O_cluster_name:           H2O_from_python_aaran_p8v51n
H2O_cluster_total_nodes:    1
H2O_cluster_free_memory:    3.542 Gb
H2O_cluster_total_cores:    8
H2O_cluster_allowed_cores:  8
H2O_cluster_status:         locked, healthy
H2O_connection_url:         http://127.0.0.1:54321
H2O_connection_proxy:       {"http": null, "https": null}
H2O_internal_security:      False
Python_version:             3.10.8 final
--------------------------  -----------------------------

In [3]:
#load data
df = pd.read_csv('duke_vital_model_imputed.csv')
df.head()
df["PostCond"].value_counts()
df["PostCond"] = df["PostCond"].apply(lambda x: 0 if x == 1 else 1)

In [4]:
subj_dict = tools.create_subj_dict(df)
subj_labels = np.array([np.array(list([key, subj_dict[key][0]["PostCond"]])) for key in subj_dict.keys()])
# subject_ids = subj_conds[:, 0]
# subject_labels = subj_conds[:, 1]
skf = StratifiedKFold(n_splits = 10, shuffle=True, random_state=42)
patient_split = skf.split(subj_labels[:, 0], subj_labels[:, 1])
train_patient_index = dict()
test_patient_index = dict()
cnt = 0
for train_i, test_i in patient_split:
    train_patient_index[cnt] = train_i
    test_patient_index[cnt] = test_i
    cnt += 1

In [5]:
def filterer(pair):
    key, value = pair
    if len(value) >= 2:
        return True
    return False

In [6]:
train_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[train_patient_index[0], 0]}
test_subj_dict = {patient: subj_dict[patient] for patient in subj_dict.keys() if patient in subj_labels[test_patient_index[0], 0]}

train_df = tools.subj_dict_to_df(train_subj_dict)
test_df = tools.subj_dict_to_df(test_subj_dict)

trends = tools.return_trends(train_df, [[2], [3], [4], [5], [6], [7], [8], [9], [10], [11], [12], [13]], ["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

train_col_names = list(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())
test_col_names = list(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())

imputer = IterativeImputer(random_state=42)

X_train_for_imputed = imputer.fit_transform(train_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())
X_test_for_imputed = imputer.transform(test_df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())

imputed_train_df = pd.DataFrame(X_train_for_imputed, columns=train_col_names)
imputed_test_df = pd.DataFrame(X_test_for_imputed, columns=test_col_names)

imputed_train_df["RSUBJID"] = train_df["RSUBJID"]
imputed_train_df["PostCond"] = train_df["PostCond"]
imputed_test_df["RSUBJID"] = test_df["RSUBJID"]
imputed_test_df["PostCond"] = test_df["PostCond"]

imputed_train_subj_dict = tools.create_subj_dict(imputed_train_df)
imputed_test_subj_dict = tools.create_subj_dict(imputed_test_df)

filtered_imputed_train_subj_dict = dict(filter(filterer, imputed_train_subj_dict.items()))
filtered_imputed_test_subj_dict = dict(filter(filterer, imputed_test_subj_dict.items()))

normalized_train_dict = tools.dist_from_age_mean(filtered_imputed_train_subj_dict, trends)
normalized_test_dict = tools.dist_from_age_mean(filtered_imputed_test_subj_dict, trends)

linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
linearized_test_dict = tools.dict_to_linfit(normalized_test_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])

linearized_train_df = tools.lin_dict_to_df(linearized_train_dict)
linearized_test_df = tools.lin_dict_to_df(linearized_test_dict)

X = linearized_train_df.drop(labels=["RSUBJID"], axis=1)
X_test = linearized_test_df.drop(labels=["RSUBJID"], axis=1)

# trends = tools.return_trends(df, [[2], [3], [4], [5], [6], [7], [8], [9], [10], [11], [12], [13]], ["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
# train_col_names = list(df.drop(labels=["RSUBJID", "PostCond"], axis=1).keys())
# imputer = IterativeImputer(random_state=42)
# X_train_for_imputed = imputer.fit_transform(df.drop(labels=["RSUBJID", "PostCond"], axis=1).to_numpy())
# imputed_train_df = pd.DataFrame(X_train_for_imputed, columns=train_col_names)
# imputed_train_df["RSUBJID"] = df["RSUBJID"]
# imputed_train_df["PostCond"] = df["PostCond"]
# imputed_train_subj_dict = tools.create_subj_dict(imputed_train_df)
# filtered_imputed_train_subj_dict = dict(filter(filterer, imputed_train_subj_dict.items()))
# normalized_train_dict = tools.dist_from_age_mean(filtered_imputed_train_subj_dict, trends)
# linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
# linearized_train_df = tools.lin_dict_to_df(linearized_train_dict)
# X = linearized_train_df.drop(labels=["RSUBJID"], axis=1)


/var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/ipykernel_88951/3185170000.py:34: RankWarning: Polyfit may be poorly conditioned
  linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
/var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/ipykernel_88951/3185170000.py:34: RankWarning: Polyfit may be poorly conditioned
  linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGHT_R", "CREATININE_R", "HDL_R", "LDL_R", "TOTCHOL_R", "wbc", "gluc", "tprot", "alb", "ast", "alt", "tbil", "cr", "ptinr"])
/var/folders/yv/fxtprh2s52j94nnjg1219s_w0000gn/T/ipykernel_88951/3185170000.py:34: RankWarning: Polyfit may be poorly conditioned
  linearized_train_dict = tools.dict_to_linfit(normalized_train_dict, trend_cols=["DIASBP_R", "PULSE_R", "SYSBP_R", "WEIGH

In [7]:
categorical_columns = ["RACE_G", "GENDER", "HXCOPD", "HXDIAB", "HXHTN", "HXHYL", "HXSMOKE"]

X["RACE_G"] = X["RACE_G"].astype(int)
X_test["RACE_G"] = X_test["RACE_G"].astype(int)

X = h2o.H2OFrame(X)
X_test = h2o.H2OFrame(X_test)

X["RACE_G"] = X["RACE_G"].asfactor()
X["GENDER"] = X["GENDER"].asfactor()
X["HXCOPD"] = X["HXCOPD"].asfactor()
X["HXDIAB"] = X["HXDIAB"].asfactor()
X["HXHTN"] = X["HXHTN"].asfactor()
X["HXHYL"] = X["HXHYL"].asfactor()
X["HXSMOKE"] = X["HXSMOKE"].asfactor()
X["PostCond"] = X["PostCond"].asfactor()

X_test["RACE_G"] = X_test["RACE_G"].asfactor()
X_test["GENDER"] = X_test["GENDER"].asfactor()
X_test["HXCOPD"] = X_test["HXCOPD"].asfactor()
X_test["HXDIAB"] = X_test["HXDIAB"].asfactor()
X_test["HXHTN"] = X_test["HXHTN"].asfactor()
X_test["HXHYL"] = X_test["HXHYL"].asfactor()
X_test["HXSMOKE"] = X_test["HXSMOKE"].asfactor()
X_test["PostCond"] = X_test["PostCond"].asfactor()

Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%
Parse progress: |████████████████████████████████████████████████████████████████| (done) 100%


In [8]:
# train, test = X.split_frame(ratios=[0.8], seed = 1)
aml = H2OAutoML(max_models =25,
                balance_classes=True,
		seed =1)

aml.train(training_frame = X, y = 'PostCond')


AutoML progress: |███████████████████████████████████████████████████████████████| (done) 100%


Model Details
=============
H2OStackedEnsembleEstimator : Stacked Ensemble
Model Key: StackedEnsemble_AllModels_1_AutoML_1_20230322_135307

No summary for this model

ModelMetricsBinomialGLM: stackedensemble
** Reported on train data. **

MSE: 0.08439307001708585
RMSE: 0.2905048536893762
LogLoss: 0.2976879061748674
AUC: 0.9807883763359636
AUCPR: 0.9125404610527665
Gini: 0.9615767526719272
Null degrees of freedom: 10033
Residual degrees of freedom: 10013
Null deviance: 11036.08036674247
Residual deviance: 5974.000901117239
AIC: 6016.000901117239

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.32574815640514426
       0     1     Error    Rate
-----  ----  ----  -------  ---------------
0      7410  226   0.0296   (226.0/7636.0)
1      119   2279  0.0496   (119.0/2398.0)
Total  7529  2505  0.0344   (345.0/10034.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max f1                       0.325748     0.929635  190
max f2                       0.30686      0.94889   198
max f0point5                 0.346109     0.921644  183
max accuracy                 0.325748     0.965617  190
max precision                0.921839     1         0
max recall                   0.144767     1         302
max specificity              0.921839     1         0
max absolute_mcc             0.325748     0.907278  190
max min_per_class_accuracy   0.309338     0.962415  197
max mean_per_class_accuracy  0.30686      0.963467  198
max tns                      0.921839     7636      0
max fns                      0.921839     2397      0
max fps                      0.00213271   7636      399
max tps                      0.144767     2398      302
max tnr                      0.921839     1         0
max fnr                      0.921839     0.999583  0
max fpr                      0.00213271   1         399
max tpr                      0.144767     1         302

Gains/Lift Table: Avg response rate: 23.90 %, avg score: 24.93 %
group    cumulative_data_fraction    lower_threshold    lift        cumulative_lift    response_rate    score      cumulative_response_rate    cumulative_score    capture_rate    cumulative_capture_rate    gain      cumulative_gain    kolmogorov_smirnov
-------  --------------------------  -----------------  ----------  -----------------  ---------------  ---------  --------------------------  ------------------  --------------  -------------------------  --------  -----------------  --------------------
1        0.0100658                   0.814478           4.18432     4.18432            1                0.828702   1                           0.828702            0.0421184       0.0421184                  318.432   318.432            0.0421184
2        0.0200319                   0.802681           4.18432     4.18432            1                0.807897   1                           0.818351            0.0417014       0.0838198                  318.432   318.432            0.0838198
3        0.029998                    0.792638           4.18432     4.18432            1                0.797304   1                           0.811358            0.0417014       0.125521                   318.432   318.432            0.125521
4        0.0400638                   0.782681           4.18432     4.18432            1                0.787735   1                           0.805423            0.0421184       0.16764                    318.432   318.432            0.16764
5        0.0500299                   0.769211           4.14248     4.17598            0.99             0.776888   0.998008                    0.799739            0.0412844       0.208924                   314.248   317.598            0.208793
6        0.10006                     0.55351            2.85901     3.5175             0.683267         0.659372   0.840637                    0.729555            0.143036        0.35196          

In [9]:
lb = aml.leaderboard
lb.head(rows=lb.nrows)

model_id                                                      auc    logloss     aucpr    mean_per_class_error      rmse       mse
-------------------------------------------------------  --------  ---------  --------  ----------------------  --------  --------
StackedEnsemble_AllModels_1_AutoML_1_20230322_135307     0.728492   0.469514  0.501996                0.342438  0.387167  0.149899
StackedEnsemble_BestOfFamily_1_AutoML_1_20230322_135307  0.727775   0.469479  0.505316                0.340303  0.387019  0.149784
GBM_5_AutoML_1_20230322_135307                           0.722047   0.473836  0.505621                0.3458    0.38889   0.151236
GBM_grid_1_AutoML_1_20230322_135307_model_3              0.720087   0.474892  0.500032                0.350279  0.389492  0.151704
GBM_1_AutoML_1_20230322_135307                           0.719448   0.475707  0.497475                0.349554  0.389761  0.151913
GBM_2_AutoML_1_20230322_135307                           0.718599   0.475186  0.498968                0.347534  0.389256  0.151521
GBM_grid_1_AutoML_1_20230322_135307_model_2              0.718346   0.474692  0.500649                0.35209   0.389496  0.151707
GBM_3_AutoML_1_20230322_135307                           0.717551   0.476842  0.496644                0.35192   0.389977  0.152082
GBM_4_AutoML_1_20230322_135307                           0.711167   0.483562  0.491339                0.357197  0.392201  0.153821
XRT_1_AutoML_1_20230322_135307                           0.710966   0.492015  0.496337                0.354492  0.394312  0.155482
GBM_grid_1_AutoML_1_20230322_135307_model_4              0.709117   0.484755  0.491529                0.356066  0.39286   0.154339
DRF_1_AutoML_1_20230322_135307                           0.707408   0.495969  0.489631                0.355551  0.395527  0.156442
XGBoost_grid_1_AutoML_1_20230322_135307_model_1          0.706354   0.498958  0.484167                0.353917  0.397703  0.158167
GBM_grid_1_AutoML_1_20230322_135307_model_1              0.705236   0.494966  0.486548                0.3602    0.395644  0.156534
XGBoost_grid_1_AutoML_1_20230322_135307_model_4          0.704288   0.496137  0.484876                0.35448   0.397313  0.157858
XGBoost_grid_1_AutoML_1_20230322_135307_model_3          0.70381    0.502731  0.484042                0.358726  0.399338  0.159471
XGBoost_3_AutoML_1_20230322_135307                       0.700221   0.5684    0.489594                0.361385  0.437539  0.191441
XGBoost_grid_1_AutoML_1_20230322_135307_model_2          0.699506   0.507981  0.480781                0.360733  0.40073   0.160585
DeepLearning_grid_3_AutoML_1_20230322_135307_model_1     0.693871   0.512133  0.435604                0.367503  0.405563  0.164481
XGBoost_1_AutoML_1_20230322_135307                       0.692019   0.571866  0.467336                0.366085  0.430931  0.185702
XGBoost_grid_1_AutoML_1_20230322_135307_model_5          0.689377   0.538707  0.463299                0.367168  0.409671  0.16783
DeepLearning_grid_2_AutoML_1_20230322_135307_model_1     0.687962   0.519981  0.421801                0.367628  0.408634  0.166982
DeepLearning_1_AutoML_1_20230322_135307                  0.685261   0.515775  0.417316                0.370082  0.406879  0.165551
XGBoost_2_AutoML_1_20230322_135307                       0.682264   0.574503  0.466834                0.382801  0.433666  0.188066
DeepLearning_grid_1_AutoML_1_20230322_135307_model_1     0.670604   0.574003  0.351755                0.368309  0.419677  0.176128
GLM_1_AutoML_1_20230322_135307                           0.665742   0.515981  0.333511                0.373509  0.412796  0.170401
DeepLearning_grid_1_AutoML_1_20230322_135307_model_2     0.662421   0.540692  0.336081                0.375541  0.415606  0.172729
[27 rows x 7 columns]

In [15]:
dl = h2o.get_model("DeepLearning_grid_3_AutoML_1_20230322_135307_model_1")
print(dl)

Model Details
H2ODeepLearningEstimator : Deep Learning
Model Key: DeepLearning_grid_3_AutoML_1_20230322_135307_model_1


Status of Neuron Layers: predicting PostCond, 2-class classification, bernoulli distribution, CrossEntropy loss, 29,002 weights/biases, 355.9 KB, 1,699,783 training samples, mini-batch size 1
    layer    units    type              dropout    l1    l2    mean_rate              rate_rms              momentum    mean_weight            weight_rms           mean_bias             bias_rms
--  -------  -------  ----------------  ---------  ----  ----  ---------------------  --------------------  ----------  ---------------------  -------------------  --------------------  -------------------
    1        85       Input             15.0
    2        100      RectifierDropout  10.0       0.0   0.0   0.09134000278863053    0.2682383060455322    0.0         -0.006602251679394827  0.22262585163116455  -0.0934585740146775   0.249289870262146
    3        100      RectifierDropou

In [10]:
best_model = aml.get_best_model()
print(best_model)

Model Details
H2OStackedEnsembleEstimator : Stacked Ensemble
Model Key: StackedEnsemble_AllModels_1_AutoML_1_20230322_135307

No summary for this model

ModelMetricsBinomialGLM: stackedensemble
** Reported on train data. **

MSE: 0.08439307001708585
RMSE: 0.2905048536893762
LogLoss: 0.2976879061748674
AUC: 0.9807883763359636
AUCPR: 0.9125404610527665
Gini: 0.9615767526719272
Null degrees of freedom: 10033
Residual degrees of freedom: 10013
Null deviance: 11036.08036674247
Residual deviance: 5974.000901117239
AIC: 6016.000901117239

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.32574815640514426
       0     1     Error    Rate
-----  ----  ----  -------  ---------------
0      7410  226   0.0296   (226.0/7636.0)
1      119   2279  0.0496   (119.0/2398.0)
Total  7529  2505  0.0344   (345.0/10034.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max

In [11]:
best_model.model_performance(X_test)

ModelMetricsBinomialGLM: stackedensemble
** Reported on test data. **

MSE: 0.15138414430330357
RMSE: 0.38908115387834397
LogLoss: 0.47050043485328946
AUC: 0.7343220322641604
AUCPR: 0.4781033831904685
Gini: 0.46864406452832075
Null degrees of freedom: 1700
Residual degrees of freedom: 1680
Null deviance: 1850.866605141788
Residual deviance: 1600.6424793708907
AIC: 1642.6424793708907

Confusion Matrix (Act/Pred) for max f1 @ threshold = 0.24966234329797612
       0     1    Error    Rate
-----  ----  ---  -------  --------------
0      958   345  0.2648   (345.0/1303.0)
1      161   237  0.4045   (161.0/398.0)
Total  1119  582  0.2975   (506.0/1701.0)

Maximum Metrics: Maximum metrics at their respective thresholds
metric                       threshold    value     idx
---------------------------  -----------  --------  -----
max f1                       0.249662     0.483673  183
max f2                       0.113767     0.646537  322
max f0point5                 0.397335     0.529126  79
max accuracy                 0.410695     0.801293  75
max precision                0.825728     1         0
max recall                   0.0381743    1         389
max specificity              0.825728     1         0
max absolute_mcc             0.397335     0.344587  79
max min_per_class_accuracy   0.223842     0.653266  207
max mean_per_class_accuracy  0.209554     0.667432  220
max tns                      0.825728     1303      0
max fns                      0.825728     397       0
max fps                      0.023992     1303      399
max tps                      0.0381743    398       389
max tnr                      0.825728     1         0
max fnr                      0.825728     0.997487  0
max fpr                      0.023992     1         399
max tpr                      0.0381743    1         389

Gains/Lift Table: Avg response rate: 23.40 %, avg score: 23.70 %
group    cumulative_data_fraction    lower_threshold    lift      cumulative_lift    response_rate    score      cumulative_response_rate    cumulative_score    capture_rate    cumulative_capture_rate    gain      cumulative_gain    kolmogorov_smirnov
-------  --------------------------  -----------------  --------  -----------------  ---------------  ---------  --------------------------  ------------------  --------------  -------------------------  --------  -----------------  --------------------
1        0.010582                    0.802919           2.61181   2.61181            0.611111         0.811382   0.611111                    0.811382            0.0276382       0.0276382                  161.181   161.181            0.022266
2        0.0205761                   0.790431           2.51404   2.56432            0.588235         0.797605   0.6                         0.80469             0.0251256       0.0527638                  151.404   156.432            0.0420194
3        0.0305703                   0.776268           2.76544   2.63007            0.647059         0.781436   0.615385                    0.797088            0.0276382       0.080402                   176.544   163.007            0.0650528
4        0.0405644                   0.76777            3.51966   2.84925            0.823529         0.771422   0.666667                    0.790764            0.0351759       0.115578                   251.966   184.925            0.0979263
5        0.0505585                   0.752232           3.51966   2.98177            0.823529         0.758729   0.697674                    0.784432            0.0351759       0.150754                   251.966   198.177            0.1308
6        0.100529                    0.382017           2.71516   2.84925            0.635294         0.585902   0.666667                    0.685747            0.135678        0.286432                   171.516   184.925            0.242687
7        0.1505                      0.328527           1.10618   2.27049            0.258824         0.350393   0.53125                     0.5

In [12]:
model_path = h2o.save_model(model=best_model,path='/Users/aaran/MHA_Upload_my_changes/Duke_Dataset/slope_model', force=True)
print(model_path)


/Users/aaran/MHA_Upload_my_changes/Duke_Dataset/slope_model/StackedEnsemble_AllModels_1_AutoML_1_20230322_135307


In [13]:
explain_model = aml.explain(frame = test, figsize = (8,6))

NameError: name 'test' is not defined